In [1]:
import sys
sys.path.append("../src")
import os
import datetime
import pandas as pd
import numpy as np
from example_lorenz import get_lorenz_data
from sindy_utils import library_size
from training import train_network
import torch
print(torch.cuda.is_available())


True


# Generate data

In [2]:
# generate training, validation, testing data
noise_strength = 1e-6
training_data = get_lorenz_data(1024, noise_strength=noise_strength)
validation_data = get_lorenz_data(20, noise_strength=noise_strength)
training_data['x'] = torch.tensor(training_data['x']).float().to('cuda')
training_data['dx'] = torch.tensor(training_data['dx']).float().to('cuda')
training_data['t'] = torch.tensor(training_data['t']).float().to('cuda')
training_data['z'] = torch.tensor(training_data['z']).float().to('cuda')
training_data['dz'] = torch.tensor(training_data['dz']).float().to('cuda')
training_data['ddx'] = None

validation_data['x'] = torch.tensor(validation_data['x']).float().to('cuda')
validation_data['dx'] = torch.tensor(validation_data['dx']).float().to('cuda')
validation_data['t'] = torch.tensor(validation_data['t']).float().to('cuda')
validation_data['z'] = torch.tensor(validation_data['z']).float().to('cuda')
validation_data['dz'] = torch.tensor(validation_data['dz']).float().to('cuda')
validation_data['ddx'] = None


# Set up model and training parameters

In [3]:
params = {}

params['input_dim'] = 128
params['latent_dim'] = 3
params['model_order'] = 1
params['poly_order'] = 3
params['include_sine'] = False
params['library_dim'] = library_size(params['latent_dim'], params['poly_order'], params['include_sine'], True)

# sequential thresholding parameters
params['sequential_thresholding'] = True
params['coefficient_threshold'] = 0.1
params['threshold_frequency'] = 500
params['coefficient_mask'] = torch.ones((params['library_dim'], params['latent_dim']))
params['coefficient_initialization'] = 'constant'

# loss function weighting
params['loss_weight_decoder'] = 1.0
params['loss_weight_sindy_z'] = 0
params['loss_weight_sindy_x'] = 1e-4
params['loss_weight_sindy_regularization'] = 1e-5

params['activation'] = 'sigmoid'
params['widths'] = [64, 32]
print(params['widths'][::-1])
# training parameters
params['epoch_size'] = training_data['x'].shape[0]
params['batch_size'] = 1024
params['learning_rate'] = 2e-3

params['data_path'] = os.getcwd() + '/'
params['print_progress'] = True
params['print_frequency'] = 1

# training time cutoffs
params['max_epochs'] = 5001
params['refinement_epochs'] = 1001

[32, 64]


In [4]:
import numpy as np
import torch

def to_numpy(obj):
    if isinstance(obj, torch.Tensor):
        return obj.cpu().numpy()  # Convert tensor to numpy array
    elif isinstance(obj, dict):
        return {k: to_numpy(v) for k, v in obj.items()}  # Apply recursively to dictionaries
    elif isinstance(obj, list):
        return [to_numpy(v) for v in obj]  # Apply recursively to lists
    else:
        return obj  # Return the object as is if it's neither a tensor, list, nor dictionary


# Run training experiments

In [5]:
num_experiments = 1
df = pd.DataFrame()
for i in range(num_experiments):
    print('EXPERIMENT %d' % i)

    params['coefficient_mask'] = torch.ones((params['library_dim'], params['latent_dim']))

    params['save_name'] = 'lorenz_' + datetime.datetime.now().strftime("%Y_%m_%d_%H_%M_%S_%f")
    
    results_dict = train_network(training_data, validation_data, params)
    results_dict = to_numpy(results_dict)
    params = to_numpy(params)

    df = df._append({**results_dict, **params}, ignore_index=True)

df.to_pickle('experiment_results_' + datetime.datetime.now().strftime("%Y%m%d%H%M") + '.pkl')

EXPERIMENT 0
Device: cuda:0


c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\../src\training.py:181: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'x': torch.tensor(data['x'][idxs], dtype=torch.float32).to(params['device']),
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\../src\training.py:182: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'dx': torch.tensor(data['dx'][idxs], dtype=torch.float32).to(params['device']),
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\../src\training.py:188: UserWarn

TRAINING
Epoch 0
   Training Total Loss: 0.02339758910238743
   Training decoder Loss: 0.021980267018079758
   Training sindy_z Loss: 1386.9818115234375
   Training sindy_x Loss: 14.086453437805176
   Training sindy_regularization Loss: 0.8676080107688904
   Validation Total Loss: 0.01956525631248951
   Validation decoder Loss: 0.018233081325888634
   Validation sindy_z Loss: 920.1142578125
   Validation sindy_x Loss: 13.234980583190918
   Validation sindy_regularization Loss: 0.8676080107688904
Decoder Loss Ratio: 0.096034, Decoder SINDy Loss Ratio: 1.093535
Epoch 1
   Training Total Loss: 0.0094315055757761
   Training decoder Loss: 0.008659662678837776
   Training sindy_z Loss: 208.53041076660156
   Training sindy_x Loss: 7.647231101989746
   Training sindy_regularization Loss: 0.711950957775116
   Validation Total Loss: 0.008194205351173878
   Validation decoder Loss: 0.007385544944554567
   Validation sindy_z Loss: 176.34864807128906
   Validation sindy_x Loss: 8.015400886535645
 

c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\../src\training.py:59: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  loss_val, _, _ = autoencoder_network.define_loss(torch.tensor(train_dict['x'], dtype=torch.float32), torch.tensor(train_dict['dx'], dtype=torch.float32), train_dict['ddx'], params=params)


Epoch 0
   Training Total Loss: 2.5041714252438396e-05
   Training decoder Loss: 1.8178583559347317e-05
   Training sindy_z Loss: 4.928842067718506
   Training sindy_x Loss: 0.013166036456823349
   Training sindy_regularization Loss: 0.5546528100967407
   Validation Total Loss: 3.472504613455385e-05
   Validation decoder Loss: 2.6277297365595587e-05
   Validation sindy_z Loss: 5.984960556030273
   Validation sindy_x Loss: 0.029012199491262436
   Validation sindy_regularization Loss: 0.5546528100967407
Decoder Loss Ratio: 0.000138, Decoder SINDy Loss Ratio: 0.002397
Epoch 1
Epoch 1
   Training Total Loss: 4.068320777150802e-05
   Training decoder Loss: 3.366365490364842e-05
   Training sindy_z Loss: 5.2236738204956055
   Training sindy_x Loss: 0.014657720923423767
   Training sindy_regularization Loss: 0.5553781390190125
   Validation Total Loss: 4.88077275804244e-05
   Validation decoder Loss: 4.0520288166590035e-05
   Validation sindy_z Loss: 6.852780342102051
   Validation sindy_x Lo

c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\../src\training.py:73: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  loss_val, final_losses, _ = autoencoder_network.define_loss(torch.tensor(validation_dict['x'], dtype=torch.float32), torch.tensor(validation_dict['dx'], dtype=torch.float32),validation_dict['ddx'], params=params)
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\../src\training.py:75: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  _, _, _, _, _, _, _, sindy_predict = autoencoder_network(torch.tensor(validation_dict['x'], dtype=tor

In [6]:
print(results_dict)
    
print(params)

{'num_epochs': 5000, 'x_norm': array(0.18986021, dtype=float32), 'sindy_predict_norm_x': array(12.102934, dtype=float32), 'sindy_predict_norm_z': 145.79493713378906, 'sindy_coefficients': array([[ 6.8237551e-04, -6.7856157e-04,  6.2720227e+00],
       [-3.1897923e-01,  8.2265310e+00,  1.0399134e-03],
       [ 1.1923362e-03, -3.1426020e+00,  3.2225917e-03],
       [ 1.3786734e-03,  4.5214660e-05, -1.1489758e+00],
       [-6.3017379e-03,  3.4499925e-03, -1.6949447e-02],
       [ 9.6772835e-03,  5.3171343e-03, -2.9791229e+00],
       [ 1.8796757e-01, -8.3530508e-03,  2.8846183e-04],
       [-2.3208286e-03,  1.8172868e-03, -2.2432795e-01],
       [ 7.1542263e+00,  2.9811111e-01,  1.7866815e-03],
       [-7.4909470e-04,  2.8289231e-03,  1.0001340e-02],
       [-7.3436443e-03,  2.5623132e-02, -3.3173487e-03],
       [-4.6699759e-02, -4.8926763e-02, -1.1107506e-04],
       [-3.7814605e-03, -8.4101213e-03, -8.2938699e-03],
       [-1.6029572e-02, -1.4503515e-02, -1.2475821e-03],
       [ 7.086